## Data cleaning

In [1]:
import pandas as pd

In [2]:
data = pd.read_csv('/Users/yunlei/Desktop/MGMT 478/Combined dataset_nonsort.csv')

In [3]:
data.head()

STATION                                        NAME  LATITUDE  \
0  USW00014835  LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   
1  USW00014835  LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   
2  USW00014835  LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   
3  USW00014835  LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   
4  USW00014835  LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   

   LONGITUDE  ELEVATION     DATE  AWND  PRCP  SNOW  TAVG  TMAX  TMIN  
0  -86.94739      181.7  2010-01   8.5  1.01   NaN  23.5  29.5  17.5  
1  -86.94739      181.7  2010-02   7.6  0.61   NaN    26  32.8  19.1  
2  -86.94739      181.7  2010-03   7.2  3.22   NaN  44.8  55.1  34.6  
3  -86.94739      181.7  2010-04   8.1  2.49   NaN  58.1  70.4  45.8  
4  -86.94739      181.7  2010-05   6.7  5.55   NaN  64.7  75.2  54.2

In [4]:
from sklearn.impute import SimpleImputer

In [5]:
# Convert DATE column to datetime format
data['DATE'] = pd.to_datetime(data['DATE'])

In [6]:
# Extract year and month from DATE as new features
data['YEAR'] = data['DATE'].dt.year
data['MONTH'] = data['DATE'].dt.month

In [7]:
# Drop the 'SNOW' column
data_cleaned = data.drop(['SNOW'], axis=1)

In [8]:
# Convert non-numeric to numeric
for column in ['LATITUDE','LONGITUDE','ELEVATION','AWND', 'TAVG', 'TMAX', 'TMIN']:
    data_cleaned[column] = pd.to_numeric(data_cleaned[column], errors='coerce')

In [9]:
# Imputer missing data as median of the column
imputer = SimpleImputer(strategy='median')
data_cleaned[['AWND', 'TAVG', 'TMAX', 'TMIN']] = imputer.fit_transform(data_cleaned[['AWND', 'TAVG', 'TMAX', 'TMIN']])

In [10]:
data_cleaned.head()

STATION                                        NAME  LATITUDE  \
0  USW00014835  LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   
1  USW00014835  LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   
2  USW00014835  LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   
3  USW00014835  LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   
4  USW00014835  LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   

   LONGITUDE  ELEVATION       DATE  AWND  PRCP  TAVG  TMAX  TMIN  YEAR  MONTH  
0  -86.94739      181.7 2010-01-01   8.5  1.01  23.5  29.5  17.5  2010      1  
1  -86.94739      181.7 2010-02-01   7.6  0.61  26.0  32.8  19.1  2010      2  
2  -86.94739      181.7 2010-03-01   7.2  3.22  44.8  55.1  34.6  2010      3  
3  -86.94739      181.7 2010-04-01   8.1  2.49  58.1  70.4  45.8  2010      4  
4  -86.94739      181.7 2010-05-01   6.7  5.55  64.7  75.2  54.2  2010      5

## Using a specific weather station to predict

### Get six near weather station around the specific weather station

In [11]:
import numpy as np
from sklearn.neighbors import NearestNeighbors

stations = data_cleaned[['STATION', 'NAME', 'LATITUDE', 'LONGITUDE']].drop_duplicates()
coordinates = stations[['LATITUDE', 'LONGITUDE']]
neighbors_model = NearestNeighbors(n_neighbors=6)
neighbors_model.fit(coordinates)

def six_nearest_weather_stations(latitude, longitude):
    query_coordinates = np.array([[latitude, longitude]])
    distances, indices = neighbors_model.kneighbors(query_coordinates)
    nearest_stations_info = stations.iloc[indices[0]].copy() 
    nearest_stations_info['DISTANCE(°)'] = distances[0]

    return nearest_stations_info

### Get the average value for the near weather station exclude the one used as predicted weather station

In [12]:
def average_values_for_nearest_stations_exclude(latitude, longitude, station_to_exclude):
    nearest_stations_info = six_nearest_weather_stations(latitude, longitude)
    nearest_station_ids = nearest_stations_info['STATION'].tolist()
    
    # Remove the specific station ID from the list
    if station_to_exclude in nearest_station_ids:
        nearest_station_ids.remove(station_to_exclude)
    
    filtered_data = data_cleaned[data_cleaned['STATION'].isin(nearest_station_ids)]
    average_values = filtered_data.groupby(['YEAR', 'MONTH'])[['AWND', 'PRCP', 'TAVG', 'TMAX', 'TMIN']].mean().reset_index()
    average_values.rename(columns={
        'AWND': 'AWND_avg',
        'PRCP': 'PRCP_avg',
        'TAVG': 'TAVG_avg',
        'TMAX': 'TMAX_avg',
        'TMIN': 'TMIN_avg'
    }, inplace=True)
    return average_values

### Expand the dataset

In [13]:
def get_analysis_data(latitude, longitude, weather_station):
    weather_station_data = data_cleaned[data_cleaned['STATION']== weather_station]
    
    for var in ['AWND', 'PRCP', 'TAVG', 'TMAX', 'TMIN']:
        for year in range(1, 6):
            year_lag = year*12
            weather_station_data[f'{var}_lag_{year}_year'] = weather_station_data[var].shift(year_lag)
            
    neighbor_data = average_values_for_nearest_stations_exclude(latitude, longitude, weather_station)
    merged_data = pd.merge(weather_station_data, neighbor_data, on=['YEAR', 'MONTH'], how='inner')
    
    for var in ['AWND_avg', 'PRCP_avg', 'TAVG_avg', 'TMAX_avg', 'TMIN_avg']:
        for year in range(1, 6):
            year_lag = year*12
            merged_data[f'{var}_lag_{year}_year'] = merged_data[var].shift(year_lag)
    
    merged_data_final = merged_data.drop(columns=['AWND', 'TAVG', 'TMAX', 'TMIN', 'AWND_avg', 'PRCP_avg', 'TAVG_avg', 'TMAX_avg', 'TMIN_avg'])
    merged_data_final = merged_data_final.dropna()
    return merged_data_final

### Lasso: top 5 feature selection

In [14]:
from sklearn.linear_model import LassoCV
from sklearn.metrics import mean_squared_error
import numpy as np
import pandas as pd

def lasso_mse(latitude, longitude, weather_station):
    
    merged_data_final = get_analysis_data(latitude, longitude, weather_station)
    
    # Initialize dictionaries to store MSE values for each year and top features for each year
    mse_values = {}
    top_features_per_year = {}

    # Initialize lists to accumulate actual and predicted values for all years
    all_actuals = []
    all_predictions = []

    # Set the starting and ending years for the time window
    years = merged_data_final['YEAR'].unique()
    start_year = years[0] + 4
    end_year = 2022

    # Loop through each time window
    for year in range(start_year, end_year + 1):
        # Define the training and testing sets
        train_df = merged_data_final[merged_data_final['YEAR'].between(year - 4, year)]
        test_df = merged_data_final[merged_data_final['YEAR'] == year + 1]

        # Remove rows with missing values
        train_df = train_df.dropna()
        test_df = test_df.dropna()

        # Select features and target variable
        X_train = train_df.drop(columns=['STATION', 'NAME', 'LATITUDE', 'LONGITUDE', 'ELEVATION', 'DATE', 'PRCP', 'YEAR'])
        y_train = train_df['PRCP']
        X_test = test_df[X_train.columns]
        y_test = test_df['PRCP']

        # Use LassoCV for feature selection and model fitting
        lasso = LassoCV(cv=5).fit(X_train, y_train)

        # Predict using the model
        y_pred = lasso.predict(X_test)

        # Calculate and store the MSE value
        mse = mean_squared_error(y_test, y_pred)
        mse_values[year] = mse

        # Accumulate actual and predicted values for all years
        all_actuals.extend(y_test.tolist())
        all_predictions.extend(y_pred.tolist())

        # Get feature importance and store the top 5 features for the year
        feature_importance = np.abs(lasso.coef_)
        feature_names = X_train.columns
        features_coef = zip(feature_names, feature_importance)
        top_features = sorted(features_coef, key=lambda x: x[1], reverse=True)[:5]
        top_features_per_year[year] = top_features

    # After looping, calculate the overall MSE
    overall_mse = mean_squared_error(all_actuals, all_predictions)
    
    return overall_mse, top_features_per_year, mse_values

In [21]:
six_nearest_weather_stations(40.41236,-86.94739)

/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(


STATION                                        NAME  LATITUDE  \
0    USW00014835  LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   
671  USW00093819   INDIANAPOLIS INTERNATIONAL AIRPORT, IN US  39.72515   
336  USC00120784       BLOOMINGTON INDIANA UNIVERSITY, IN US  39.17399   
839  USW00053866        SHELBYVILLE MUNICIPAL AIRPORT, IN US  39.58545   
168  USW00014848                   SOUTH BEND AIRPORT, IN US  41.70722   
503  USW00014827     FORT WAYNE INTERNATIONAL AIRPORT, IN US  40.97248   

     LONGITUDE  DISTANCE(°)  
0    -86.94739     0.000000  
671  -86.28160     0.956835  
336  -86.52076     1.309799  
839  -85.79982     1.414460  
168  -86.31628     1.440473  
503  -85.20636     1.828912

In [15]:
lasso_mse(40.41236,-86.94739,'USW00014835') # Purdue Airport

/var/folders/cr/ls79phkx4vb_rmnkc6h2ddqh0000gn/T/ipykernel_55258/2382662988.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  weather_station_data[f'{var}_lag_{year}_year'] = weather_station_data[var].shift(year_lag)
/var/folders/cr/ls79phkx4vb_rmnkc6h2ddqh0000gn/T/ipykernel_55258/2382662988.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  weather_station_data[f'{var}_lag_{year}_year'] = weather_station_data[var].shift(year_lag)
/var/folders/cr/ls79phkx4vb_rmnkc6h2ddqh0000gn/T/ipykernel_55258/238266298

(2.826690816017955,
 {2019: [('TMAX_avg_lag_5_year', 0.015984805522539773),
   ('TMIN_avg_lag_4_year', 0.014951699641251497),
   ('TMAX_avg_lag_1_year', 0.0028454409837878484),
   ('TMIN_avg_lag_2_year', 0.0015757316578251285),
   ('MONTH', 0.0)],
  2020: [('AWND_lag_3_year', 0.39271750767856595),
   ('PRCP_avg_lag_5_year', 0.11456147717977933),
   ('PRCP_avg_lag_2_year', 0.11141771746245449),
   ('TMAX_avg_lag_5_year', 0.060176181547590774),
   ('MONTH', 0.05526634031870445)],
  2021: [('AWND_lag_3_year', 0.34514623806514166),
   ('PRCP_avg_lag_2_year', 0.15594311744078962),
   ('PRCP_lag_5_year', 0.1355051282386049),
   ('TMAX_lag_5_year', 0.05757569403810059),
   ('TMIN_lag_1_year', 0.03938697132423715)],
  2022: [('TMAX_avg_lag_5_year', 0.00832102190311387),
   ('TMAX_avg_lag_3_year', 0.0045407089496747165),
   ('TMAX_lag_4_year', 0.0026677178414137087),
   ('MONTH', 0.0),
   ('AWND_lag_1_year', 0.0)]},
 {2019: 1.2695958784998593,
  2020: 4.020866242015131,
  2021: 2.69070383861950

In [22]:
six_nearest_weather_stations(41.96017,-87.93164)

/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(


STATION                                        NAME  LATITUDE  \
1345  USW00094846  CHICAGO OHARE INTERNATIONAL AIRPORT, IL US  41.96017   
1176  USW00094892  CHICAGO WEST CHICAGO DUPAGE AIRPORT, IL US  41.89641   
168   USW00014848                   SOUTH BEND AIRPORT, IN US  41.70722   
0     USW00014835  LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   
671   USW00093819   INDIANAPOLIS INTERNATIONAL AIRPORT, IN US  39.72515   
503   USW00014827     FORT WAYNE INTERNATIONAL AIRPORT, IN US  40.97248   

      LONGITUDE  DISTANCE(°)  
1345  -87.93164     0.000000  
1176  -88.25119     0.325849  
168   -86.31628     1.635045  
0     -86.94739     1.834247  
671   -86.28160     2.778119  
503   -85.20636     2.898738

In [16]:
lasso_mse(41.96017,-87.93164,'USW00094846') # Chicago Ohare

/var/folders/cr/ls79phkx4vb_rmnkc6h2ddqh0000gn/T/ipykernel_55258/2382662988.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  weather_station_data[f'{var}_lag_{year}_year'] = weather_station_data[var].shift(year_lag)
/var/folders/cr/ls79phkx4vb_rmnkc6h2ddqh0000gn/T/ipykernel_55258/2382662988.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  weather_station_data[f'{var}_lag_{year}_year'] = weather_station_data[var].shift(year_lag)
/var/folders/cr/ls79phkx4vb_rmnkc6h2ddqh0000gn/T/ipykernel_55258/238266298

(3.8851132723315303,
 {2019: [('TMAX_avg_lag_1_year', 0.04048233585222285),
   ('TMIN_avg_lag_4_year', 0.00978297674467683),
   ('TMAX_avg_lag_2_year', 0.0019051123467602755),
   ('MONTH', 0.0),
   ('AWND_lag_1_year', 0.0)],
  2020: [('PRCP_lag_4_year', 0.20022629336150197),
   ('AWND_avg_lag_3_year', 0.09958285151586614),
   ('TMAX_avg_lag_5_year', 0.08090544751553164),
   ('TMIN_lag_1_year', 0.07075923474625219),
   ('TMAX_avg_lag_1_year', 0.05104656795828298)],
  2021: [('TMIN_lag_1_year', 0.18711917231905925),
   ('TMAX_avg_lag_1_year', 0.1573890931875127),
   ('PRCP_lag_4_year', 0.04625408065929011),
   ('TMAX_lag_2_year', 0.03164099613291713),
   ('TMAX_avg_lag_5_year', 0.031012387715844334)],
  2022: [('TMIN_lag_1_year', 0.2099726708000364),
   ('TMAX_avg_lag_1_year', 0.16104221629068696),
   ('TMAX_avg_lag_2_year', 0.04396844474180958),
   ('TMAX_avg_lag_5_year', 0.03637171340526726),
   ('TMIN_lag_4_year', 0.007017955161902739)]},
 {2019: 4.816189706868612,
  2020: 4.606804181

In [24]:
station_counts = data_cleaned.groupby('STATION').size()

In [30]:
station_counts

STATION
USC00114355    168
USC00116011    120
USC00120784    167
USC00174193    119
USC00174927    121
USW00014606    121
USW00014827    168
USW00014835    168
USW00014848    168
USW00023174    169
USW00023188    169
USW00023234    169
USW00053866    168
USW00054772    121
USW00093193    169
USW00093225    169
USW00093810    169
USW00093819    168
USW00094626    121
USW00094846    169
USW00094892    169
dtype: int64

### Loop all the valid weather stations

Filter weather stations if it has records from 2010 to 2023.

In [33]:
stations_with_enough_records = station_counts[station_counts >= 167].index

In [34]:
valid_stations = data_cleaned[
    (data_cleaned['YEAR'] == 2010) & 
    (data_cleaned['STATION'].isin(stations_with_enough_records))
][['STATION', 'NAME', 'LATITUDE', 'LONGITUDE']].drop_duplicates()

In [36]:
valid_stations 

STATION                                         NAME  LATITUDE  \
0     USW00014835   LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   
168   USW00014848                    SOUTH BEND AIRPORT, IN US  41.70722   
336   USC00120784        BLOOMINGTON INDIANA UNIVERSITY, IN US  39.17399   
503   USW00014827      FORT WAYNE INTERNATIONAL AIRPORT, IN US  40.97248   
671   USW00093819    INDIANAPOLIS INTERNATIONAL AIRPORT, IN US  39.72515   
839   USW00053866         SHELBYVILLE MUNICIPAL AIRPORT, IN US  39.58545   
1007  USW00093810  CARBONDALE SOUTHERN ILLINOIS AIRPORT, IL US  37.78329   
1176  USW00094892   CHICAGO WEST CHICAGO DUPAGE AIRPORT, IL US  41.89641   
1345  USW00094846   CHICAGO OHARE INTERNATIONAL AIRPORT, IL US  41.96017   
1514  USC00114355                  ILLINOIS CITY DAM 16, IL US  41.42550   
2405  USW00023174     LOS ANGELES INTERNATIONAL AIRPORT, CA US  33.93816   
2574  USW00023234   SAN FRANCISCO INTERNATIONAL AIRPORT, CA US  37.61962   
2743  USW00023188       SAN DIEGO INTERNATIONAL AIRPORT, CA US  32.73360   
2912  USW00093225       SACRAMENTO METROPOLITAN AIRPORT, CA US  38.70069   
3081  USW00093193         FRESNO YOSEMITE INTERNATIONAL, CA US  36.77999   

      LONGITUDE  
0     -86.94739  
168   -86.31628  
336   -86.52076  
503   -85.20636  
671   -86.28160  
839   -85.79982  
1007  -89.24533  
1176  -88.25119  
1345  -87.93164  
1514  -91.00940  
2405 -118.38660  
2574 -122.36562  
2743 -117.18310  
2912 -121.59479  
3081 -119.72016

In [37]:
valid_stations['overall_mse'] = valid_stations.apply(lambda row: lasso_mse(row['LATITUDE'], row['LONGITUDE'], row['STATION']), axis=1)

/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(
/opt/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 7.635e-02, tolerance: 1.202e-02
  model = cd_fast.enet_coordinate_descent(
/opt/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.725e-02, tolerance: 1.202e-02
  model = cd_fast.enet_coordinate_descent(
/opt/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Ob

In [38]:
valid_stations

STATION                                         NAME  LATITUDE  \
0     USW00014835   LAFAYETTE PURDUE UNIVERSITY AIRPORT, IN US  40.41236   
168   USW00014848                    SOUTH BEND AIRPORT, IN US  41.70722   
336   USC00120784        BLOOMINGTON INDIANA UNIVERSITY, IN US  39.17399   
503   USW00014827      FORT WAYNE INTERNATIONAL AIRPORT, IN US  40.97248   
671   USW00093819    INDIANAPOLIS INTERNATIONAL AIRPORT, IN US  39.72515   
839   USW00053866         SHELBYVILLE MUNICIPAL AIRPORT, IN US  39.58545   
1007  USW00093810  CARBONDALE SOUTHERN ILLINOIS AIRPORT, IL US  37.78329   
1176  USW00094892   CHICAGO WEST CHICAGO DUPAGE AIRPORT, IL US  41.89641   
1345  USW00094846   CHICAGO OHARE INTERNATIONAL AIRPORT, IL US  41.96017   
1514  USC00114355                  ILLINOIS CITY DAM 16, IL US  41.42550   
2405  USW00023174     LOS ANGELES INTERNATIONAL AIRPORT, CA US  33.93816   
2574  USW00023234   SAN FRANCISCO INTERNATIONAL AIRPORT, CA US  37.61962   
2743  USW00023188       SAN DIEGO INTERNATIONAL AIRPORT, CA US  32.73360   
2912  USW00093225       SACRAMENTO METROPOLITAN AIRPORT, CA US  38.70069   
3081  USW00093193         FRESNO YOSEMITE INTERNATIONAL, CA US  36.77999   

      LONGITUDE                                        overall_mse  
0     -86.94739  (2.826690816017955, {2019: [('TMAX_avg_lag_5_y...  
168   -86.31628  (3.26156817175176, {2019: [('TMAX_avg_lag_1_ye...  
336   -86.52076  (5.064375014568086, {2019: [('MONTH', 0.0), ('...  
503   -85.20636  (2.15800046698172, {2019: [('TMIN_avg_lag_2_ye...  
671   -86.28160  (3.5996865574216375, {2019: [('TMAX_lag_3_year...  
839   -85.79982  (3.6225832454022675, {2019: [('TMIN_lag_2_year...  
1007  -89.24533  (5.469349032032115, {2019: [('TMIN_avg_lag_1_y...  
1176  -88.25119  (3.9810843895128336, {2019: [('TMAX_avg_lag_4_...  
1345  -87.93164  (3.8851132723315303, {2019: [('TMAX_avg_lag_1_...  
1514  -91.00940  (1.9506695493408632, {2019: [('TMIN_lag_2_year...  
2405 -118.38660  (3.320010859592196, {2019: [('TMIN_avg_lag_3_y...  
2574 -122.36562  (5.372550528659975, {2019: [('TMIN_avg_lag_4_y...  
2743 -117.18310  (1.096816411876359, {2019: [('TMIN_avg_lag_5_y...  
2912 -121.59479  (3.3211039622113057, {2019: [('MONTH', 0.06722...  
3081 -119.72016  (1.6352788598732053, {2019: [('TAVG_avg_lag_4_...